# Quantum Mechanics Analysis (3D)

Time independent Schrodinger equation in 3D:
$$ -\frac{\hbar^2}{2m} \left(\frac{\partial^2\psi}{\partial x^2} +\frac{\partial^2\psi}{\partial y^2} +\frac{\partial^2\psi}{\partial z^2}\right) + V(x)\psi(x) = E \psi(x) $$

Kinetic Energy Operator (matrix):
$$ T = -\frac{\hbar^2}{2m} \left[ (I\otimes D)\otimes I + (I\otimes I)\otimes D + (D\otimes I)\otimes I \right] $$
where,
$$ D = \begin{bmatrix}
-2 & 1 & 0 & \ldots & 0 \\
1 & -2 & 1 & \ldots & 0 \\
0 & 1 & -2 & \ldots & 0 \\
\vdots & \vdots & \vdots & \ddots & \vdots \\
0 & 0 & 0 & \ldots & -2
\end{bmatrix} $$
Hamiltonian Operator (matrix):
$$ H = T + V $$
The Schrodinger equation is;
$$ H\psi = E\psi $$

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from scipy.linalg import eigh
import scipy.constants as const
from scipy import sparse
from scipy.sparse.linalg import eigsh

In [2]:
hcut = 1
mass = 1
# hcut = const.hbar
# mass = const.electron_mass

L = 4
# L = 50e-9  # Domain size
N = 25  # Number of grid points
x = np.linspace(-L, L, N)
y = np.linspace(-L, L, N)
z = np.linspace(-L, L, N)
X, Y, Z = np.meshgrid(x, y, z)

## Potentials

### Potential Well:
$$ V(x, y, z) = 0 \quad ; \quad -L_x<x<L_x,\,-L_y<y<L_y,\,-L_z<z<L_z $$
$$ = V_0 \quad ; \quad otherwise $$

### 3D LHO Potential:
$$ V(x) = \frac{1}{2} m(\omega_x^2 x^2 + \omega_y^2 y^2 + \omega_z^2 z^2) $$

In [3]:
# potential
def potential3d(x, y, z, omega_x, omega_y, omega_z):
    return 0.5*mass*(omega_x**2 *x**2 +omega_y**2 *y**2 +omega_z**2 *z**2)

wx, wy, wz = 1.0, 1.0, 1.0 # INPUT
# [wx, wy, wz] = np.array([12, 12, 12])*const.electron_volt/const.hbar  # INPUT

Vxyz = potential3d(X, Y, Z, wx, wy, wz)

In [4]:
isoval = np.abs(Vxyz).max() * 0.6
fig1 = go.Figure(data=go.Isosurface(
    x = X.flatten(),
    y = Y.flatten(),
    z = Z.flatten(),
    value = Vxyz.flatten(),
    isomin = -isoval,
    isomax = isoval,
    opacity = 0.4, # CHANGE
    surface_count = 2,
    colorscale = 'Viridis'))

fig1.update_layout(
                title=f'3D LHO Potential',
                scene=dict(xaxis_title='x', yaxis_title='y', zaxis_title='z'))
fig1.show()

### Hydrogen atom problem

## Solution of eigenvalue equation

### Using **`eigh`**

### Using **`eigsh`**

In [5]:
dx = x[1] - x[0]
dy = y[1] - y[0]
dz = z[1] - z[0]
diags = np.array([np.ones(N), -2*np.ones(N), np.ones(N)])
D = sparse.spdiags(diags, np.array([-1,0,1]), N, N)
T_x = -hcut**2/(2*mass) * (1/dx**2) * D
T_y = -hcut**2/(2*mass) * (1/dx**2) * D
T_z = -hcut**2/(2*mass) * (1/dx**2) * D
T = (sparse.kron(sparse.kron(sparse.eye(N), T_x), sparse.eye(N)) + 
        sparse.kron(sparse.kron(sparse.eye(N), sparse.eye(N)), T_y) + 
        sparse.kron(sparse.kron(T_z, sparse.eye(N)), sparse.eye(N)))

V = sparse.diags(Vxyz.flatten(), 0)
H = T + V
eigenvals, eigenvecsT = eigsh(H, k=50, which='SM')

### Defining Functions for normalized eigenvectors

In [6]:
def eig_val(n):
    return eigenvals[n]
def eig_vec(n):
    eigf = eigenvecsT[:, n].reshape(N, N, N)
    eigfm2 = eigf.conjugate()*eigf
    eigf = eigf/np.sum(eigfm2*dx*dy*dz)**0.5
    return eigf
def prob_den(n):
    eigv = eigenvals[n]
    eigf = eigenvecsT[:, n].reshape(N, N, N)
    eigfm2 = eigf.conjugate()*eigf
    eigf = eigf/np.sum(eigfm2*dx*dy*dz)**0.5
    eigfm2 = eigf.conjugate()*eigf
    return eigfm2


### Overview of Solution

In [7]:
np.sum(prob_den(4)*dx*dy*dz)

1.0

In [8]:
for i in range(20):
    print(f'n={i}, E{i}={eig_val(i)}')

n=0, E0=1.4895096203096703
n=1, E1=2.4754220595946355
n=2, E2=2.475422059594651
n=3, E3=2.4754220595946723
n=4, E4=3.447001695717232
n=5, E5=3.4470016957172414
n=6, E6=3.447001695717254
n=7, E7=3.4613344988796597
n=8, E8=3.4613344988796744
n=9, E9=3.461334498879683
n=10, E10=4.404044516363307
n=11, E11=4.404044516363333
n=12, E12=4.404044516363418
n=13, E13=4.43291413500219
n=14, E14=4.4329141350022025
n=15, E15=4.43291413500221
n=16, E16=4.432914135002224
n=17, E17=4.432914135002233
n=18, E18=4.43291413500226
n=19, E19=4.447246938164622


### Plot for a state

**cmap**: 'Accent', 'Accent_r', 'Blues', 'Blues_r', 'BrBG', 'BrBG_r', 'BuGn', 'BuGn_r', 'BuPu', 'BuPu_r', 'CMRmap', 'CMRmap_r', 'Dark2', 'Dark2_r', 'GnBu', 'GnBu_r', 'Greens', 'Greens_r', 'Greys', 'Greys_r', 'OrRd', 'OrRd_r', 'Oranges', 'Oranges_r', 'PRGn', 'PRGn_r', 'Paired', 'Paired_r', 'Pastel1', 'Pastel1_r', 'Pastel2', 'Pastel2_r', 'PiYG', 'PiYG_r', 'PuBu', 'PuBuGn', 'PuBuGn_r', 'PuBu_r', 'PuOr', 'PuOr_r', 'PuRd', 'PuRd_r', 'Purples', 'Purples_r', 'RdBu', 'RdBu_r', 'RdGy', 'RdGy_r', 'RdPu', 'RdPu_r', 'RdYlBu', 'RdYlBu_r', 'RdYlGn', 'RdYlGn_r', 'Reds', 'Reds_r', 'Set1', 'Set1_r', 'Set2', 'Set2_r', 'Set3', 'Set3_r', 'Spectral', 'Spectral_r', 'Wistia', 'Wistia_r', 'YlGn', 'YlGnBu', 'YlGnBu_r', 'YlGn_r', 'YlOrBr', 'YlOrBr_r', 'YlOrRd', 'YlOrRd_r', 'afmhot', 'afmhot_r', 'autumn', 'autumn_r', 'binary', 'binary_r', 'bone', 'bone_r', 'brg', 'brg_r', 'bwr', 'bwr_r', 'cividis', 'cividis_r', 'cool', 'cool_r', 'coolwarm', 'coolwarm_r', 'copper', 'copper_r', 'cubehelix', 'cubehelix_r', 'flag', 'flag_r', 'gist_earth', 'gist_earth_r', 'gist_gray', 'gist_gray_r', 'gist_heat', 'gist_heat_r', 'gist_ncar', 'gist_ncar_r', 'gist_rainbow', 'gist_rainbow_r', 'gist_stern', 'gist_stern_r', 'gist_yarg', 'gist_yarg_r', 'gnuplot', 'gnuplot2', 'gnuplot2_r', 'gnuplot_r', 'gray', 'gray_r', 'hot', 'hot_r', 'hsv', 'hsv_r', 'inferno', 'inferno_r', 'jet', 'jet_r', 'magma', 'magma_r', 'nipy_spectral', 'nipy_spectral_r', 'ocean', 'ocean_r', 'pink', 'pink_r', 'plasma', 'plasma_r', 'prism', 'prism_r', 'rainbow', 'rainbow_r', 'seismic', 'seismic_r', 'spring', 'spring_r', 'summer', 'summer_r', 'tab10', 'tab10_r', 'tab20', 'tab20_r', 'tab20b', 'tab20b_r', 'tab20c', 'tab20c_r', 'terrain', 'terrain_r', 'turbo', 'turbo_r', 'twilight', 'twilight_r', 'twilight_shifted', 'twilight_shifted_r', 'viridis', 'viridis_r', 'winter', 'winter_r'

Use **`eig_vec(n)`** for the plotting of wavefunctions and use **`prob_den(n)`** for the plotting of probability densities.

In [12]:
n = 5   # INPUT

isoval = np.abs(eig_vec(n)).max() * 0.6
fig1 = go.Figure(data=go.Isosurface(
    x = X.flatten(),
    y = Y.flatten(),
    z = Z.flatten(),
    value = eig_vec(n).flatten(),
    isomin = -isoval,
    isomax = isoval,
    opacity = 0.4, # CHANGE
    surface_count = 2,
    colorscale = 'Viridis'))

fig1.update_layout(
                title=f'Excited State Isosurface Plot (State {n}) - Energy: {eig_val(n):.4}',
                scene=dict(xaxis_title='x', yaxis_title='y', zaxis_title='z'))
fig1.show()

## Superposition

In [10]:
ns = np.array([0,3,7,11,14,19])  # INPUT
cs = np.array([10, 6, 4, 5, 4, 7])   # INPUT
cs = cs/np.sum(cs**2)**0.5

psis = eig_vec(0)*0
for i in range(ns.size):
    psii = cs[i]*eig_vec(ns[i])
    psis += psii

In [11]:
for i in range(len(ns)):
    print(f'state = {ns[i]} \t corresponding ratio = {cs[i]}')

isoval = np.abs(psis).max() * 0.6
fig1 = go.Figure(data=go.Isosurface(
    x = X.flatten(),
    y = Y.flatten(),
    z = Z.flatten(),
    value = psis.flatten(),
    isomin = -isoval,
    isomax = isoval,
    opacity = 0.4, # CHANGE
    surface_count = 2,
    colorscale = 'Viridis'))

fig1.update_layout(
                title=f'Superposed state',
                scene=dict(xaxis_title='x', yaxis_title='y', zaxis_title='z'))
fig1.show()

state = 0 	 corresponding ratio = 0.6428243465332251
state = 3 	 corresponding ratio = 0.38569460791993504
state = 7 	 corresponding ratio = 0.25712973861329
state = 11 	 corresponding ratio = 0.32141217326661253
state = 14 	 corresponding ratio = 0.25712973861329
state = 19 	 corresponding ratio = 0.44997704257325755
